<a href="https://colab.research.google.com/github/824zzy/Code_Chips/blob/master/Chinese_segmentation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Copyright 2018 The BUPT Zhengyuan Zhu.

Licensed under the Apache License, Version 2.0 (the "License").
<table class="tfo-notebook-buttons" align="center"><td>


<td>
<a target="_blank"  href="https://github.com/BUPT/awesome-chatbot/tree/master/code"><img width=32px src="https://www.tensorflow.org/images/GitHub-Mark-32px.png" />View all sources on GitHub</a></td>
</table>
# Chinese Segmentation Based on Maximum Probability

## References:
 - [Origin corpus from internet: https://github.com/hankcs/OpenCorpus](https://github.com/hankcs/OpenCorpus)
 - [Bigram: https://en.wikipedia.org/wiki/Bigram](https://en.wikipedia.org/wiki/Bigram)
 - [Viterbi Algorithm](https://en.wikipedia.org/wiki/Viterbi_algorithm)
 - [n-gram](https://en.wikipedia.org/wiki/N-gram)
 - [max probability chinese segmentation](https://blog.csdn.net/qijingpei/article/details/79330491)
 - [MP-segmentation](https://github.com/nan1104/MP-segmentation/blob/master/segmentation.py)
 - [NLP Viterbi 算法应用之Unigrams，Bigrams](https://www.jianshu.com/p/4b466728ec4d)
 - [动态规划(DP)的整理-Python描述
](https://blog.csdn.net/MrLevo520/article/details/75676160)

## Prepare Data
According to slides presented by Professor Wang. It is convenient to use Beijing University's corpus which can be found [here](https://github.com/hankcs/OpenCorpus). 

This project is going to do some experiments on this corpus. So let's get start!

### Download corpus from Internet
We could download `1998 people news in January` corpus into your colab via `wget` command.

**Note that** all the files your download from internet to virtual machine will be deleted when over 14 hours!

In [1]:
! wget https://github.com/hankcs/OpenCorpus/raw/master/pku98/199801.txt

--2018-12-13 03:27:00--  https://github.com/hankcs/OpenCorpus/raw/master/pku98/199801.txt
Resolving github.com (github.com)... 192.30.253.112, 192.30.253.113
Connecting to github.com (github.com)|192.30.253.112|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/hankcs/OpenCorpus/master/pku98/199801.txt [following]
--2018-12-13 03:27:06--  https://raw.githubusercontent.com/hankcs/OpenCorpus/master/pku98/199801.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 9004042 (8.6M) [text/plain]
Saving to: ‘199801.txt’

199801.txt          100%[===================>]   8.59M  9.92MB/s    in 0.9s    

2018-12-13 03:27:07 (9.92 MB/s) - ‘199801.txt’ saved [9004042/9004042]



## Functions for data cleaning



In [17]:
import codecs
import chardet

def read_lines(corpus_name, encode_type='utf-8'):
  """Read lines from different corpus
  
  # Arguments:
    corpus_name: str in corpus list
  
  # Return:
    lines: a list contains the whole corpus
  """
  
  with codecs.open(corpus_name, 'r', encoding=encode_type) as file:
    lines = file.readlines()

  return lines


# test case for loading corpus
f = open('199801.txt', 'rb')
data = f.read()
print("the format of corpus is: ", chardet.detect(data))
lines = read_lines("199801.txt")
print("Examples of corpus 1998 People News:")
print("First sentence of corpus:", lines[0])
print("Second sentence of corpus:", lines[1])

the format of corpus is:  {'encoding': 'utf-8', 'confidence': 0.99, 'language': ''}
Examples of corpus 1998 People News:
First sentence of corpus: 迈向/v	充满/v	希望/n	的/u	新/a	世纪/n	——/w	一九九八年/t	新年/t	讲话/n	（/w	附/v	图片/n	１/m	张/q	）/w

Second sentence of corpus: 中共中央/nt	总书记/n	、/w	国家/n	主席/n	江泽民/nr



### Build dictionary: word counts dictionary and bi-gram dictionary
The origin corpus need to be clean. Notice that in each sentence,  words are seperated by `tab` and tagged by default. 

Our goal of this function is  to build a dictionary that wipe off all the tagging and the other no meaning chars.

In [20]:
def build_dictionary(corpus):
  """Build a dictonary based on differnet corpus for finding candidate words
  
  # Arguments:
    corpus: a list contains all sentences in corpus
    
  # Return:
    word_count_dict: a dictionary whose key represents the word and value 
                     represents the count of its occurrence. 
  """
  word_count_dict = {}
  i = 0
  for index, sentence in enumerate(corpus):
    if index == 0:
      print("Example of sentence in corpus: ", sentence)
    # seperate word by tab
    word_list = [word for word in sentence.split("\t")]
    if index == 0:
      print("seperate word by tab: ", word_list)
      print("----------")
    # drop tagging in word
    for i, word in enumerate(word_list):
      word_list[i] = word.split('/')[0]
      if index == 0:
        print("Word examples of splited by the backslash", word_list[i])     
    # build dictionary via sentence
    for word in word_list:
      if word_count_dict.get(word) != None:
        word_count_dict[word] += 1
      else:
        word_count_dict[word] = 1
        
  return word_count_dict

# build dictonary using people news
word_count_dict = build_dictionary(lines)

Example of sentence in corpus:  迈向/v	充满/v	希望/n	的/u	新/a	世纪/n	——/w	一九九八年/t	新年/t	讲话/n	（/w	附/v	图片/n	１/m	张/q	）/w

seperate word by tab:  ['迈向/v', '充满/v', '希望/n', '的/u', '新/a', '世纪/n', '——/w', '一九九八年/t', '新年/t', '讲话/n', '（/w', '附/v', '图片/n', '１/m', '张/q', '）/w\n']
----------
Word examples of splited by the backslash 迈向
Word examples of splited by the backslash 充满
Word examples of splited by the backslash 希望
Word examples of splited by the backslash 的
Word examples of splited by the backslash 新
Word examples of splited by the backslash 世纪
Word examples of splited by the backslash ——
Word examples of splited by the backslash 一九九八年
Word examples of splited by the backslash 新年
Word examples of splited by the backslash 讲话
Word examples of splited by the backslash （
Word examples of splited by the backslash 附
Word examples of splited by the backslash 图片
Word examples of splited by the backslash １
Word examples of splited by the backslash 张
Word examples of splited by the backslash ）


### Build bigram dictionary
For the sake of accerlating Bigram Model and reducing the time spending during computing probability. We need to build a dictionary to record Bigram word pairs.

In [21]:
def bigram_dictionary(corpus):
  """Build Bigram dictionary by corpus
  The key is a bigram, and The value is times of bigram occurance.
  
  # Arguments:
    corpus: a list contains all sentences in corpus
  
  # Returns:
    bigram_dict: a dictionary whose key represents the word and value 
                 represents the count of its occurrence. 
  
  """
  bigram_dict = {}
  for epi, sentence in enumerate(corpus):
    # seperate word by tab
    word_list = [word for word in sentence.split("\t")]
    # drop tagging in word
    for i, word in enumerate(word_list):
      word_list[i] = word.split('/')[0]
    # build bigram count for dictionary
    for pos, word in enumerate(word_list):
      if pos < len(word_list) - 1:
        bigram = word_list[pos] + ' ' + word_list[pos + 1]
        if bigram_dict.get(bigram) != None:
          bigram_dict[bigram] += 1
        else:
          bigram_dict[bigram] = 1
    if epi == 0:
      print("Example of bigram dictionary in first sentence:\n", bigram_dict)
  return bigram_dict
          
bigram_dict = bigram_dictionary(lines)
print("We have ", len(bigram_dict), " bigram pairs!!")


Example of bigram dictionary in first sentence:
 {'迈向 充满': 1, '充满 希望': 1, '希望 的': 1, '的 新': 1, '新 世纪': 1, '世纪 ——': 1, '—— 一九九八年': 1, '一九九八年 新年': 1, '新年 讲话': 1, '讲话 （': 1, '（ 附': 1, '附 图片': 1, '图片 １': 1, '１ 张': 1, '张 ）': 1}
We have  458507  bigram pairs!!


## N-gram model
### What is N-gram model?
In the fields of computational linguistics and probability, an n-gram is a contiguous sequence of n items from a given sample of text or speech. The items can be phonemes, syllables, letters, words or base pairs according to the application.

### What is Bigram?
A bigram or digram is a sequence of two adjacent elements from a string of tokens, which are typically letters, syllables, or words. A bigram is an n-gram for n=2. The frequency distribution of every bigram in a string is commonly used for simple statistical analysis of text in many applications, including in computational linguistics, cryptography, speech recognition, and so on.

Gappy bigrams or skipping bigrams are word pairs which allow gaps (perhaps avoiding connecting words, or allowing some simulation of dependencies, as in a dependency grammar).

Head word bigrams are gappy bigrams with an explicit dependency relationship.

Bigrams help provide the conditional probability of a token given the preceding token, when the relation of the conditional probability is applied:

$$P(W_n|W_{n-1})=\frac{P(W_{n-1}, W_n)}{P(W_{n-1})}$$

That is, the probability $P()$ of a token $W_{n}$ given the preceding token $W_{{n-1}}$ is equal to the probability of their bigram, or the co-occurrence of the two tokens $P(W_{{n-1}},W_{n})$, divided by the probability of the preceding token.

### Build a class with Bi-gram Model
The details of Bi-gram Model have writen on the comments of each function. The code style is learning from Keras. 

In [0]:
import numpy as np
import re

class BiGram(object):
  """Apply N-Gram model to Bigram.
  
  A bigram or digram is a sequence of two adjacent elements from a string of 
  tokens, which are typically letters, syllables, or words. 
  A bigram is an n-gram for n=2. The frequency distribution of every bigram in 
  a string is commonly used for simple statistical analysis of text in many 
  applications, including in computational linguistics, cryptography, speech 
  recognition, and so on.
  
  # Arguments:
    corpus:
    word_count_dict:
    bigram_dict: 
    max_split: a int numrepresenting the sliding window's size
    word_num: a int num representing length of dictionary's words
    
  # References:
    - [Bigram](https://en.wikipedia.org/wiki/Bigram)
  
  """
  
  
  def __init__(self, corpus, word_count_dict, bigram_dict, max_split=4):
    self.corpus = corpus
    self.word_count_dict = word_count_dict
    self.max_split = max_split
    self.bigram_dict = bigram_dict
    self.word_num = len(word_count_dict)
    
    
  def split_sentence(self, sentence):
    """ reduce calculation complexity through split the sentence into small one.
        split subsentence according to punctuation
    
    # Aruguments:
      sentence: a str represents the sentence to be splitted
      
    # Returns:
      split_list: a list of sentences containing the split results
    """
    split_list = []
                   
    com_sens = sentence.split('，')
    for com_sen in com_sens:
      if com_sen != com_sens[-1]:
        com_sen += '，'
        
      stop_sens = com_sen.split('。')      
      for stop_sen in stop_sens:
        if stop_sen != stop_sens[-1]:
          stop_sen += '。'
        
        pause_sens = stop_sen.split('、')
        for pause_sen in pause_sens:
          if pause_sen != pause_sens[-1]:
            pause_sen += '、'
          
          l_brack_sens = pause_sen.split('（')
          for l_brack_sen in l_brack_sens:
            if l_brack_sen != l_brack_sens[-1]:
              l_brack_sen += '（'
            
            r_brack_sens = l_brack_sen.split('）')
            for r_brack_sen in r_brack_sens:
              if r_brack_sen != r_brack_sens[-1]:
                r_brack_sen += '）'
            
              semi_sens = r_brack_sen.split('；')
              for semi_sen in semi_sens:
                if semi_sen == semi_sens[-1]:
                  split_list.append(semi_sen)
                else:
                  split_list.append(semi_sen+"；")                    
            
            
            
          
#           semi_sens = pause_sen.split('；')
#           for semi_sen in semi_sens:
#             if semi_sen == semi_sens[-1]:
#               split_list.append(semi_sen)
#             else:
#               split_list.append(semi_sen+"；")        
              
    return split_list

  def candidate_words(self, sentence):
    """scan the whole sentence from left to right, we will obtain candidate 
    words for determining left-neighbor words.
    And saving postions of each candidate words for the next step

    # Arguments:
      sentence: str, content of corpus

    # Returns:
      candidate_words: a list of candidate words.
    """
    candidate_words = []

    # search the whole sentence
    start_pos = 0
    while start_pos < len(sentence):
      word = sentence[start_pos]
      candidate_words.append([word, start_pos, start_pos])
      # check out the range of object sentence
      for max_pos in range(1, self.max_split):
        current_pos = start_pos + max_pos
        if current_pos < len(sentence):
          word = word + sentence[current_pos]
          # add words according to dictionary and num list!
          if word in self.word_count_dict.keys():
            candidate_words.append([word, start_pos, current_pos])

      start_pos += 1
            
    return candidate_words
  
  def probable_segments(self, sentence):
    """generate all probable segments based on candidate words 
    and index of words.
    # Arguments:
      sentence: a str to be scaned to segment.
      
    # Returns:
      possible_segments: a list contains all possible segment results.
      
    # Example:
      Given sentence: 太阳当空照，江泽民对我笑
      You will obstain: ['太 阳 当空 照 ， 江 泽民 对 我 笑', '太 阳 当空 照 ， 
      江 泽 民 对 我 笑', '太阳 当空 照 ， 江泽民 对 我 笑', .etc]    
    """
    # get candidate words
    candidate_words = self.candidate_words(sentence)
    c = 0

    for word in candidate_words:
    # find the first candidate word of sentence
      if c > 4000:
        break
      if word[1] == 0 and word[2] != len(sentence) - 1:
        for word in candidate_words:
          if word[1] == 0 and word[2] != len(sentence) - 1:
            end = word[2]
            for later_word in candidate_words:
              if later_word[1] == end + 1:
                word_seq = [word[0] + ' ' + later_word[0], word[1], later_word[2]]
                candidate_words.append(word_seq)
                c += 1
            candidate_words.remove(word)

    print(candidate_words)
    print(len(candidate_words))
    word_segment_res_list = []
    for seque in candidate_words:
      if seque[1] == 0:
        if seque[2] == len(sentence) - 1:
          word_segment_res_list.append(seque[0])
          
    return word_segment_res_list
  
  
  def log_prob(self, sequence, display=False):
    """Avoiding overflow from computing probability, it is necessary to use log
       probability instead of float probability. 
       The goal is to compute the probability of a sequence of words.
       Note that we are using laplace smoothing when the bigram is not appear in
       the corpus or the word is OOV.
       
    # Arguments:
      sequence: a str that contains a word sequence to be computed.
      display: a boolean to determine whether to display or not
      
    # Returns:
      prob_total: a float number represents log probability.
    """
    word_list = sequence.split(' ')
    prob_total = 0.0
    word_start = word_list[0]
    # first word prob with laplace smooth
    if word_start in self.word_count_dict.keys():
      count = self.word_count_dict[word_start]
      d = 0
    else:
      count = 1
      d = len(sequence)

    prob_total += np.log(count / (self.word_num + d))
    # calculate Bigram Probability
    for i in range(len(word_list) - 1):
      prev_w = word_list[i]
      later_w = word_list[i+1]
      bigram = prev_w + " " + later_w
      if bigram in self.bigram_dict.keys():
        count = self.bigram_dict[bigram]
        d = 0
      else:
        count = 1
        d = len(sequence)
      prob_total += np.log(count / (self.word_num + d))
    
    prob = np.power(np.e, prob_total)
    if display:
      print('The probability of ', sequence, " is ", prob)
    
    return prob_total
  
  
  def maximum_probability(self, sequence_list, sentence_len, display=False):
    """Choose the sequence has maximum probability from all probable sequences.

    # Arguments:
      sequence_list: a sequences contains all the probable sequences.
      display: a boolean to determine whether to display or not
      
    # Returns:
      seg_result: a str represents the result
    """
    max_prob = -float('inf')
    seg_result = ""
    for seq in sequence_list:
      if len(seq.split(' ')) <= 10:
        prob = self.log_prob(seq)
        if max_prob < prob:
          max_prob, seg_result = prob, seq 
      else:
        if len(seq.split(' ')) <= sentence_len * 0.9:
          prob = self.log_prob(seq)
          if max_prob < prob:
            max_prob, seg_result = prob, seq 
    if display:
      print('The segment result whose probability is %s : %s' % (np.power(np.e, max_prob), seg_result))
    return seg_result
 
  def segment_testset(self, test_set):
    """
    """
    corpus_result = ''
    for sentence in test_set:
      print("origin sentence is:", sentence)
      tmp_result = ''
      sub_sentences = self.split_sentence(sentence)
      print("sub_sentences:", sub_sentences)
      if sub_sentences[-1] == '\r\n':
        sub_sentences = sub_sentences[:-1]
        print("regular sub:", sub_sentences)
        for sen in sub_sentences:
          prob_seqs = self.probable_segments(sen)
          max_seg = self.maximum_probability(prob_seqs, len(sen), display=True)
          # every seg need a space!
          max_seg += " "
          tmp_result += max_seg
      else:
        sen = sub_sentences[0][:-2]
        print("special sub:", sen)
        prob_seqs = self.probable_segments(sen)
        max_seg = self.maximum_probability(prob_seqs, len(sen), display=True)
        tmp_result += max_seg
        
      # line break after we complete one sentence.
      tmp_result += '\r\n'
      print('segment result of this sentence is: ', tmp_result)
      print("*" * 30)
      corpus_result += tmp_result
      
    return corpus_result
          

### Test cases for BiGram model
Codes below show that results of each function.  We make some pseudo data as input. Let's see what happened in the inner mechanism.

### Function: split_sentence

In [38]:
bigram = BiGram(lines, word_count_dict, bigram_dict, 4)
long_str = '李岚清指出，要克服困难，群策群力，千方百计使高校教职工、特别是青年教师的住房困难问题在３年内有一个较大突破。'
punc_str = "大，大的。大（得）的；大大、得的。"
print("origin long sentence: \n", long_str)
print("origin punctuation sentence: \n", punc_str)
long_sens = bigram.split_sentence(long_str)
punc_sens = bigram.split_sentence(punc_str)
print("-"*20)
print("splitted long sentences: ")
for each in long_sens:
  print(each)
print("-"*20)
print("splitted punctuation sentences: ")
for each in punc_sens:
  print(each)

origin long sentence: 
 李岚清指出，要克服困难，群策群力，千方百计使高校教职工、特别是青年教师的住房困难问题在３年内有一个较大突破。
origin punctuation sentence: 
 大，大的。大（得）的；大大、得的。
--------------------
splitted long sentences: 
李岚清指出，
要克服困难，
群策群力，
千方百计使高校教职工、
特别是青年教师的住房困难问题在３年内有一个较大突破。

--------------------
splitted punctuation sentences: 
大，
大的。
大（
得）
的；
大大、
得的。



#### Function: candidate_words

In [39]:
bigram = BiGram(lines, word_count_dict, bigram_dict, 4)
cand_w = bigram.candidate_words("太阳当空照，江泽民对我笑")
print("test caset with normal sentence:", cand_w)
cand_w = bigram.candidate_words("以１９９８年的２０００个新闻")
print("test case with numbers:", cand_w)
# cand_w = bigram.candidate_words("全国已有３０个省、自治区、直辖市和１４个中央行业主管部门成立了由一把手或主管领导挂帅的解困工作领导机构")
cand_w = bigram.candidate_words("图为吴艳艳（右）和陈妍（左）在终点庆贺胜利。")
print("test case with multi numbers:", cand_w)

test caset with normal sentence: [['太', 0, 0], ['太阳', 0, 1], ['阳', 1, 1], ['当', 2, 2], ['当空', 2, 3], ['空', 3, 3], ['照', 4, 4], ['，', 5, 5], ['江', 6, 6], ['江泽民', 6, 8], ['泽', 7, 7], ['泽民', 7, 8], ['民', 8, 8], ['对', 9, 9], ['我', 10, 10], ['笑', 11, 11]]
test case with numbers: [['以', 0, 0], ['１', 1, 1], ['１９', 1, 2], ['１９９', 1, 3], ['１９９８', 1, 4], ['９', 2, 2], ['９９', 2, 3], ['９９８', 2, 4], ['９', 3, 3], ['９８', 3, 4], ['８', 4, 4], ['年', 5, 5], ['的', 6, 6], ['２', 7, 7], ['２０', 7, 8], ['２００', 7, 9], ['２０００', 7, 10], ['０', 8, 8], ['０', 9, 9], ['０', 10, 10], ['个', 11, 11], ['新', 12, 12], ['新闻', 12, 13], ['闻', 13, 13]]
test case with multi numbers: [['图', 0, 0], ['为', 1, 1], ['吴', 2, 2], ['吴艳艳', 2, 4], ['艳', 3, 3], ['艳', 4, 4], ['（', 5, 5], ['右', 6, 6], ['）', 7, 7], ['和', 8, 8], ['陈', 9, 9], ['陈妍', 9, 10], ['妍', 10, 10], ['（', 11, 11], ['左', 12, 12], ['）', 13, 13], ['在', 14, 14], ['终', 15, 15], ['终点', 15, 16], ['点', 16, 16], ['庆', 17, 17], ['庆贺', 17, 18], ['贺', 18, 18], ['胜', 19, 19], ['胜利', 19, 

#### Function: probable_segments


In [42]:
bigram = BiGram(lines, word_count_dict, bigram_dict, 4)
# test segment
print("Basic example:")
seg_result1 = bigram.probable_segments("太阳当空照，江泽民对我笑")
print(seg_result1)
print("-----")
print("Example with number:")
seg_result2 = bigram.probable_segments("以１９９８年的２０００个新闻")
print(seg_result2)
print("-----")
print("Example with special case:")
seg_result3 = bigram.probable_segments("（右）")
print(seg_result3)
# print("\n"*2 + "-"*50 + "\n"*2)

Basic example:
[['阳', 1, 1], ['当', 2, 2], ['当空', 2, 3], ['空', 3, 3], ['照', 4, 4], ['，', 5, 5], ['江', 6, 6], ['江泽民', 6, 8], ['泽', 7, 7], ['泽民', 7, 8], ['民', 8, 8], ['对', 9, 9], ['我', 10, 10], ['笑', 11, 11], ['太 阳 当空 照 ， 江 泽民 对 我 笑', 0, 11], ['太 阳 当空 照 ， 江 泽 民 对 我 笑', 0, 11], ['太阳 当空 照 ， 江泽民 对 我 笑', 0, 11], ['太 阳 当空 照 ， 江泽民 对 我 笑', 0, 11], ['太阳 当 空 照 ， 江 泽民', 0, 8], ['太 阳 当 空 照 ， 江泽民 对 我 笑', 0, 11], ['太 阳 当 空 照 ， 江 泽民 对 我 笑', 0, 11], ['太 阳 当 空 照 ， 江 泽 民 对 我 笑', 0, 11], ['太阳 当空 照 ， 江 泽 民 对 我 笑', 0, 11], ['太阳 当 空 照 ， 江 泽 民 对 我 笑', 0, 11], ['太阳 当 空 照 ， 江泽民 对 我 笑', 0, 11], ['太阳 当空 照 ， 江 泽民 对 我 笑', 0, 11]]
26
['太 阳 当空 照 ， 江 泽民 对 我 笑', '太 阳 当空 照 ， 江 泽 民 对 我 笑', '太阳 当空 照 ， 江泽民 对 我 笑', '太 阳 当空 照 ， 江泽民 对 我 笑', '太 阳 当 空 照 ， 江泽民 对 我 笑', '太 阳 当 空 照 ， 江 泽民 对 我 笑', '太 阳 当 空 照 ， 江 泽 民 对 我 笑', '太阳 当空 照 ， 江 泽 民 对 我 笑', '太阳 当 空 照 ， 江 泽 民 对 我 笑', '太阳 当 空 照 ， 江泽民 对 我 笑', '太阳 当空 照 ， 江 泽民 对 我 笑']
-----
Example with number:
[['１', 1, 1], ['１９', 1, 2], ['１９９', 1, 3], ['１９９８', 1, 4], ['９', 2, 2], ['９９', 2, 3], [

### Function: log_prob
test computation of sentence probability.

Note that in this function, the outputs displayed  are tranform into float probability.

In [43]:
for each_seg in seg_result1:
  bigram.log_prob(each_seg, display=True)
  
print("-----")  
for each_seg in seg_result2:
  bigram.log_prob(each_seg, display=True)
  
print("-----")  
for each_seg in seg_result3:
  bigram.log_prob(each_seg, display=True)

The probability of  太 阳 当空 照 ， 江 泽民 对 我 笑  is  1.3476227612219947e-43
The probability of  太 阳 当空 照 ， 江 泽 民 对 我 笑  is  2.3077312661053972e-48
The probability of  太阳 当空 照 ， 江泽民 对 我 笑  is  1.959758893130026e-33
The probability of  太 阳 当空 照 ， 江泽民 对 我 笑  is  1.8980278463471788e-37
The probability of  太 阳 当 空 照 ， 江泽民 对 我 笑  is  3.250437275009634e-42
The probability of  太 阳 当 空 照 ， 江 泽民 对 我 笑  is  2.3077312661053972e-48
The probability of  太 阳 当 空 照 ， 江 泽 民 对 我 笑  is  3.951729925236912e-53
The probability of  太阳 当空 照 ， 江 泽 民 对 我 笑  is  2.382991468014476e-44
The probability of  太阳 当 空 照 ， 江 泽 民 对 我 笑  is  4.080744312015596e-49
The probability of  太阳 当 空 照 ， 江泽民 对 我 笑  is  3.3562687526870946e-38
The probability of  太阳 当空 照 ， 江 泽民 对 我 笑  is  1.3915240464035529e-39
-----
The probability of  以 １ ９９８ 年 的 ２０００ 个 新闻  is  3.6040055374594384e-31
The probability of  以 １ ９９８ 年 的 ２０００ 个 新 闻  is  4.937670271430203e-35
The probability of  以 １９ ９ ８ 年 的 ２０００ 个 新闻  is  8.071191789837871e-36
The probability of 

In [45]:
bigram.maximum_probability(seg_result1, 12, display=True)
bigram.maximum_probability(seg_result2, 16, display=True)
bigram.maximum_probability(seg_result3, 100, display=True)
# print("\n"*2 + "-"*50 + "\n"*2)

The segment result whose probability is 1.959758893130026e-33 : 太阳 当空 照 ， 江泽民 对 我 笑
The segment result whose probability is 1.618198459254263e-27 : 以 １９９８ 年 的 ２０００ 个 新闻
The segment result whose probability is 3.5163681335659964e-09 : （ 右 ）


'（ 右 ）'

### Measure the performance of Bi-Gram Model
the test set I have upload to github which only contains 100 lines. You can upload into Colab virtual machine from [here](https://github.com/824zzy/blogResources/blob/master/txtRestources/bigram_test.txt)

#### Download test set from Internet
Note that it is necessary to check out the formation of dataset prevent from reading messy code.

In [47]:
!wget https://github.com/824zzy/blogResources/raw/master/txtRestources/bigram_test.txt
f = open('bigram_test.txt', 'rb')
data = f.read()
print("the format of corpus is: ", chardet.detect(data))

--2018-12-13 04:53:46--  https://github.com/824zzy/blogResources/raw/master/txtRestources/bigram_test.txt
Resolving github.com (github.com)... 192.30.253.113, 192.30.253.112
Connecting to github.com (github.com)|192.30.253.113|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://raw.githubusercontent.com/824zzy/blogResources/master/txtRestources/bigram_test.txt [following]
--2018-12-13 04:53:46--  https://raw.githubusercontent.com/824zzy/blogResources/master/txtRestources/bigram_test.txt
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 151.101.0.133, 151.101.64.133, 151.101.128.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|151.101.0.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 21974 (21K) [text/plain]
Saving to: ‘bigram_test.txt.3’

bigram_test.txt.3   100%[===================>]  21.46K  --.-KB/s    in 0.02s   

2018-12-13 04:53:46 (1.25 MB/s) - ‘bigram_test.txt.3’ saved 

#### Show some cases from test set
With the result above, we should pass 'gbk' to function `read_lines`

In [48]:
# test case for loading corpus
import codecs
test_lines = read_lines('bigram_test.txt', 'gbk')

print("Examples of corpus 1998 People News:")
print("First sentence of corpus:", test_lines[0])
print("Second sentence of corpus:", test_lines[1])
print(test_lines)

Examples of corpus 1998 People News:
First sentence of corpus: 本报讯春节临近，全国各地积极开展走访慰问困难企业和特困职工的送温暖活动，并广泛动员社会各方面的力量，多渠道、多层次筹集帮困资金，共同帮助困难职工度过暂时困难，解困工作正在有计划、有重点地展开。

Second sentence of corpus: 各地党委、政府及有关部门按照党中央的部署，以高度的政治责任感抓解困工作，全国已有３０个省、自治区、直辖市和１４个中央行业主管部门成立了由一把手或主管领导挂帅的解困工作领导机构，并层层分解落实解困工作目标。今年元旦、春节期间，新疆、甘肃、吉林、湖南、山东、福建、河北、广东、湖北、天津、贵州等地，都由党政主要领导率工作组，分赴困难地区和困难企业开展了走访慰问活动。煤炭部、林业部、纺织总会、航天工业总公司、核工业总公司、兵器工业总公司、有色金属工业总公司的领导都已分赴直属特困企业，帮助解决目前所面临的问题。

['本报讯春节临近，全国各地积极开展走访慰问困难企业和特困职工的送温暖活动，并广泛动员社会各方面的力量，多渠道、多层次筹集帮困资金，共同帮助困难职工度过暂时困难，解困工作正在有计划、有重点地展开。\r\n', '各地党委、政府及有关部门按照党中央的部署，以高度的政治责任感抓解困工作，全国已有３０个省、自治区、直辖市和１４个中央行业主管部门成立了由一把手或主管领导挂帅的解困工作领导机构，并层层分解落实解困工作目标。今年元旦、春节期间，新疆、甘肃、吉林、湖南、山东、福建、河北、广东、湖北、天津、贵州等地，都由党政主要领导率工作组，分赴困难地区和困难企业开展了走访慰问活动。煤炭部、林业部、纺织总会、航天工业总公司、核工业总公司、兵器工业总公司、有色金属工业总公司的领导都已分赴直属特困企业，帮助解决目前所面临的问题。\r\n', '２８个省、市、自治区建立了帮困资金制度，为解困工作提供物质手段。各地根据实际情况，采取了不同的筹资形式。如河北等２２个省、市、自治区从个人所得税中提取一定比例，或从其它财政收入中列支一部分资金；陕西等１１个省、自治区对行业或企业工资水平高于当地社会平均工资的部分，按一定比例征收调节费；山东等１２个省、市、自治区对营业性歌厅、夜总会等高消费娱乐业，按其营业收入的一定比例提取调节费

In [60]:
bigram_test = BiGram(lines, word_count_dict, bigram_dict, 4)
result = bigram_test.segment_testset(test_lines)

origin sentence is: 本报讯春节临近，全国各地积极开展走访慰问困难企业和特困职工的送温暖活动，并广泛动员社会各方面的力量，多渠道、多层次筹集帮困资金，共同帮助困难职工度过暂时困难，解困工作正在有计划、有重点地展开。

sub_sentences: ['本报讯春节临近，', '全国各地积极开展走访慰问困难企业和特困职工的送温暖活动，', '并广泛动员社会各方面的力量，', '多渠道、', '多层次筹集帮困资金，', '共同帮助困难职工度过暂时困难，', '解困工作正在有计划、', '有重点地展开。', '\r\n']
regular sub: ['本报讯春节临近，', '全国各地积极开展走访慰问困难企业和特困职工的送温暖活动，', '并广泛动员社会各方面的力量，', '多渠道、', '多层次筹集帮困资金，', '共同帮助困难职工度过暂时困难，', '解困工作正在有计划、', '有重点地展开。']
[['报', 1, 1], ['讯', 2, 2], ['春', 3, 3], ['春节', 3, 4], ['节', 4, 4], ['临', 5, 5], ['临近', 5, 6], ['近', 6, 6], ['，', 7, 7], ['本 报 讯 春 节 临近 ，', 0, 7], ['本 报 讯 春 节 临 近 ，', 0, 7], ['本报 讯 春节 临近', 0, 6], ['本 报 讯 春节 临 近 ，', 0, 7], ['本报 讯 春 节 临近', 0, 6], ['本 报 讯 春节 临近 ，', 0, 7], ['本报 讯 春节 临 近 ，', 0, 7], ['本报 讯 春 节 临 近 ，', 0, 7]]
17
The segment result whose probability is 6.023077771903402e-22 : 本报 讯 春节 临 近 ，
[['国', 1, 1], ['各', 2, 2], ['各地', 2, 3], ['地', 3, 3], ['积', 4, 4], ['积极', 4, 5], ['极', 5, 5], ['开', 6, 6], ['开展', 6, 7], ['展', 7, 7], ['走', 8, 8], ['走访', 8, 9], ['访', 9, 9], ['慰', 10, 10]

In [61]:
print("total result is: ")
print(result)

total result is: 
本报 讯 春节 临 近 ， 全国 各地 积极 开展 走访 慰问 困难 企业 和 特 困 职工 的 送 温暖 活动 ， 并 广泛 动员 社会 各 方面 的 力量 ， 多 渠道 、 多 层次 筹集 帮困 资金 ， 共同 帮助 困难 职工 度过 暂时 困难 ， 解困 工作 正在 有 计划 、 有 重点 地 展开 。 
各地 党委 、 政府 及 有关 部门 按照 党中央 的 部署 ， 以 高度 的 政治 责任感 抓 解困 工作 ， 全 国 已 有 ３０ 个 省 、 自治区 、 直 辖 市 和 １４ 个中 央行 业 主管 部门 成立 了 由 一把手 或 主管 领导 挂帅 的 解困 工作 领导 机构 ， 并 层层 分解 落实 解困 工作 目标 。 今年 元旦 、 春节 期间 ， 新 疆 、 甘 肃 、 吉 林 、 湖 南 、 山 东 、 福 建 、 河 北 、 广 东 、 湖 北 、 天 津 、 贵 州 等 地 ， 都 由 党政 主要 领导 率 工作组 ， 分赴 困难 地区 和 困难 企业 开展 了 走访 慰问 活动 。 煤炭部 、 林业部 、 纺织 总会 、 航天 工业 总公司 、 核工业 总公司 、 兵器 工业 总公司 、 有色金属 工业 总公司 的 领导 都 已 分赴 直属 特困 企业 ， 帮助 解决 目前 所 面临 的 问题 。 
２ ８ 个 省 、 市 、 自治区 建立 了 帮困 资金 制度 ， 为 解困 工作 提供 物质 手段 。 各地 根据 实际 情况 ， 采取 了 不同 的 筹资 形式 。 如 河北 等 ２２ 个 省 、 市 、 自治区 从 个人 所得税 中 提取 一定 比例 ， 或 从 其它 财政 收入 中 列支 一部分 资金 ； 陕 西 等 １１ 个 省 、 自治区 对 行业 或 企业 工资 水平 高于 当地 社会 平均 工资 的 部分 ， 按 一定 比例 征收 调节费 ； 山 东 等 １２ 个 省 、 市 、 自治区 对 营业性 歌厅 、 夜总会 等 高 消费 娱乐业 ， 按 其 营业 收入 的 一定 比例 提取 调节费 ， 用于 帮困 资金 。 
为了 使 解困 工作 制度化 ， 并 更 具有 针对性 ， 各地 还 制定 了 筹集 帮困 资金 和 实施 生活 救助 的 具体 政策 措施 。 目 前 ， 全国 所有 的 

#### write result into txt file with different format

In [62]:
utf8_f = open('result_utf-8.txt', 'w')
utf8_f.write(result)

gbk_f = open('result_gbk.txt', 'wb')
gbk_f.write(result.encode('gbk'))

27360

#### check out the formatoin

In [58]:
utf8_f = open('result_utf-8.txt', 'rb')
data = utf8_f.read()
print(chardet.detect(data))

gbk_f = open('result_gbk.txt', 'rb')
data = gbk_f.read()
print(chardet.detect(data))

{'encoding': 'utf-8', 'confidence': 0.99, 'language': ''}
{'encoding': 'GB2312', 'confidence': 0.99, 'language': 'Chinese'}


### Extension: Apply Viterbi algorithm to Bigram Model
The Viterbi algorithm is a dynamic programming algorithm for finding the most likely sequence of hidden states—called the Viterbi path—that results in a sequence of observed events, especially in the context of Markov information sources and hidden Markov models.
[from wikipedia](https://en.wikipedia.org/wiki/Viterbi_algorithm)


In [0]:
import numpy as np

class Viterbi(BiGram):
  """Apply Viterbi algorithm to Bigram.
  
  The Viterbi algorithm is a dynamic programming algorithm for finding the most
  likely sequence of hidden states—called the Viterbi path—that results in a
  sequence of observed events, especially in the context of Markov information
  sources and hidden Markov models.
  
  # Arguments:
    corpus:
    word_count_dict:
    bigram_dict: 
    max_split: a int numrepresenting the sliding window's size
    word_num: a int num representing length of dictionary's words
    
  # References:
    - [Viterbi_algorithm](https://en.wikipedia.org/wiki/Viterbi_algorithm)
  
  """
  
  
  def __init__(self, corpus, word_count_dict, bigram_dict, max_split=4):
    self.corpus = corpus
    self.word_count_dict = word_count_dict
    self.max_split = max_split
    self.bigram_dict = bigram_dict
    self.word_num = len(word_count_dict)

  def segment_position(self, sentence):

    len_sen = len(sentence)
    
    s = np.full((len_sen, len_sen), -float('inf'))
    h = []
    for i in range(len_sen):
      for j in range(i+1):
        if j == 0:
          s[0][i] = self.log_prob(len_sen, sentence[0:i+1])
        else:
          tmp = []
          for k in range(j):
            print(sentence[j:i+1], sentence[k:j])
            print(i, j, k)
            print("---")
            tmp_s = s[k][j-1] + self.log_prob(len_sen, sentence[k:j], sentence[j:i+1])
            tmp.append(tmp_s)
          print("temp:", tmp)
          print("max:", np.max(tmp))
          print("----")
          s[j][i] = np.max(tmp)
      
      pos = np.where(s[:, i] == np.max(s[:, i]))[0][0]
      h.append(pos)

  return h

        
      

  def log_prob(self, len_sen, obs_word, con_word = None, display=False):
    count = 1

    if not con_word:
      if obs_word in self.word_count_dict.keys():
        count = self.word_count_dict[obs_word]
        prob = np.log(count / (self.word_num + len_sen))
      else:
        prob = -float('inf')
    else:
      bigram = obs_word + ' ' + con_word
      if bigram in self.bigram_dict.keys():
        count = self.bigram_dict[bigram]
        prob = np.log(count / (self.word_num + len_sen))
      else:
        if con_word or obs_word not in self.word_count_dict.keys():
          prob = -float('inf')
          
    return prob
          